# Running hyperparameter optimization on Chemprop model using RayTune

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/chemprop/chemprop/blob/main/examples/hpopting.ipynb)

In [1]:
# Install chemprop from GitHub if running in Google Colab
import os

if os.getenv("COLAB_RELEASE_TAG"):
    try:
        import chemprop
    except ImportError:
        !git clone https://github.com/chemprop/chemprop.git
        %cd chemprop
        !pip install ".[hpopt]"
        %cd examples

## Import packages

In [2]:
from pathlib import Path
import sys

import pandas as pd
from lightning import pytorch as pl
import numpy as np
import ray
from ray import tune
from ray.train import CheckpointConfig, RunConfig, ScalingConfig
from ray.train.lightning import (RayDDPStrategy, RayLightningEnvironment,
                                 RayTrainReportCallback, prepare_trainer)
from ray.train.torch import TorchTrainer
from ray.tune.search.hyperopt import HyperOptSearch
from ray.tune.search.optuna import OptunaSearch
from ray.tune.schedulers import FIFOScheduler
import torch

from chemprop import data, featurizers, models, nn

# sys.path.insert(0, '../agenticadmet')
# from raytune_extra import RayTrainReportCallback

In [3]:
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)
torch.cuda.manual_seed_all(RANDOM_SEED)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

In [4]:
input_path = Path('../data/asap/datasets/rnd_splits/split_0.csv')
num_workers = 0 # number of workers for dataloader. 0 means using main process for data loading
smiles_column = 'smiles_std' # name of the column containing SMILES strings
target_columns = ['LogHLM', 'LogMLM', 'LogD', 'LogKSOL', 'LogMDR1-MDCKII'] # list of names of the columns containing targets

hpopt_save_dir = Path('../output/asap/rnd_splits/chemprop/run_0/split_0/hpopt') # directory to save hyperopt results
hpopt_save_dir.mkdir(exist_ok=True)

## Load data

In [5]:
df_input = pd.read_csv(input_path)
df_input

smiles    HLM   KSOL  LogD  \
0    COC1=CC=CC(Cl)=C1NC(=O)N1CCC[C@H](C(N)=O)C1 |a...    NaN    NaN   0.3   
1    O=C(NCC(F)F)[C@H](NC1=CC2=C(C=C1Br)CNC2)C1=CC(...    NaN  333.0   2.9   
2    O=C(NCC(F)F)[C@H](NC1=CC=C2CNCC2=C1)C1=CC(Br)=...    NaN    NaN   0.4   
3    NC(=O)[C@H]1CCCN(C(=O)CC2=CC=CC3=C2C=CO3)C1 |&...    NaN  376.0   1.0   
4     CC1=CC(CC(=O)N2CCC[C@H](C(N)=O)C2)=CC=N1 |&1:11|    NaN  375.0  -0.3   
..                                                 ...    ...    ...   ...   
399        CC(C)NC[C@H](O)COC1=CC=CC2=CC=CC=C12 |&1:5|   25.5    NaN   NaN   
400               O=C(O)CC1=CC=CC=C1NC1=C(Cl)C=CC=C1Cl  216.0    NaN   NaN   
401          NCC1=CC(Cl)=CC(C(=O)NC2=CC=C3CNCC3=C2)=C1    NaN    NaN   2.0   
402        COC(=O)NC1=NC2=CC=C(C(=O)C3=CC=CC=C3)C=C2N1    NaN    NaN   2.9   
403  CC1=NC=CN1C[C@H]1CCC2=C(C1=O)C1=CC=CC=C1N2C |&...    NaN  127.0   NaN   

       MLM  MDR1-MDCKII                                         smiles_std  \
0      NaN          2.0           COc1cccc(Cl)c1NC(=O)N1CCC[C@H](C(N)=O)C1   
1      NaN          0.2  O=C(NCC(F)F)[C@H](Nc1cc2c(cc1Br)CNC2)c1cc(Cl)c...   
2      NaN          0.5  O=C(NCC(F)F)[C@H](Nc1ccc2c(c1)CNC2)c1cc(Br)cc2...   
3      NaN          8.5            NC(=O)[C@H]1CCCN(C(=O)Cc2cccc3occc23)C1   
4      NaN          0.9              Cc1cc(CC(=O)N2CCC[C@H](C(N)=O)C2)ccn1   
..     ...          ...                                                ...   
399   63.0          NaN                    CC(C)NC[C@H](O)COc1cccc2ccccc12   
400  386.0          NaN                     O=C(O)Cc1ccccc1Nc1c(Cl)cccc1Cl   
401    NaN          NaN              NCc1cc(Cl)cc(C(=O)Nc2ccc3c(c2)CNC3)c1   
402    NaN          NaN            COC(=O)Nc1nc2ccc(C(=O)c3ccccc3)cc2[nH]1   
403    NaN          NaN              Cc1nccn1C[C@H]1CCc2c(c3ccccc3n2C)C1=O   

                                          cxsmiles_std  mol_idx smiles_ext  \
0      COc1cccc(Cl)c1NC(=O)N1CCC[C@H](C(N)=O)C1 |a:16|      191     |a:16|   
1    O=C(NCC(F)F)[C@H](Nc1cc2c(cc1Br)CNC2)c1cc(Cl)c...      335     |&1:7|   
2    O=C(NCC(F)F)[C@H](Nc1ccc2c(c1)CNC2)c1cc(Br)cc2...      336     |&1:7|   
3       NC(=O)[C@H]1CCCN(C(=O)Cc2cccc3occc23)C1 |&1:3|      300     |&1:3|   
4        Cc1cc(CC(=O)N2CCC[C@H](C(N)=O)C2)ccn1 |&1:11|      249    |&1:11|   
..                                                 ...      ...        ...   
399             CC(C)NC[C@H](O)COc1cccc2ccccc12 |&1:5|       22     |&1:5|   
400                     O=C(O)Cc1ccccc1Nc1c(Cl)cccc1Cl      380        NaN   
401              NCc1cc(Cl)cc(C(=O)Nc2ccc3c(c2)CNC3)c1      303        NaN   
402            COC(=O)Nc1nc2ccc(C(=O)c3ccccc3)cc2[nH]1      166        NaN   
403       Cc1nccn1C[C@H]1CCc2c(c3ccccc3n2C)C1=O |&1:7|      268     |&1:7|   

       LogHLM    LogMLM   LogKSOL  LogMDR1-MDCKII  split  
0         NaN       NaN       NaN        0.477121    val  
1         NaN       NaN  2.523746        0.079181  train  
2         NaN       NaN       NaN        0.176091  train  
3         NaN       NaN  2.576341        0.977724  train  
4         NaN       NaN  2.575188        0.278754  train  
..        ...       ...       ...             ...    ...  
399  1.423246  1.806180       NaN             NaN    val  
400  2.336460  2.587711       NaN             NaN    val  
401       NaN       NaN       NaN             NaN  train  
402       NaN       NaN       NaN             NaN  train  
403       NaN       NaN  2.107210             NaN  train  

[404 rows x 15 columns]

## Make data points, splits, and datasets

In [6]:
train_data, val_data = [], []
for _, row in df_input.iterrows():
    dp = data.MoleculeDatapoint.from_smi(row[smiles_column], row[target_columns].values)
    if row['split'] == 'train':
        train_data.append(dp)
    elif row['split'] == 'val':
        val_data.append(dp)

In [7]:
featurizer = featurizers.SimpleMoleculeMolGraphFeaturizer()

train_dset = data.MoleculeDataset(train_data, featurizer)
# scaler = train_dset.normalize_targets()

val_dset = data.MoleculeDataset(val_data, featurizer)
# val_dset.normalize_targets(scaler)

# Define helper function to train the model

In [8]:
# def train_model(config, train_dset, val_dset, num_workers, scaler):
def train_model(config, train_dset, val_dset, num_workers):
    # config is a dictionary containing hyperparameters used for the trial
    depth = int(config["depth"])
    ffn_hidden_dim = int(config["ffn_hidden_dim"])
    ffn_num_layers = int(config["ffn_num_layers"])
    message_hidden_dim = int(config["message_hidden_dim"])
    dropout = 0.2

    train_loader = data.build_dataloader(train_dset, num_workers=num_workers, shuffle=True)
    val_loader = data.build_dataloader(val_dset, num_workers=num_workers, shuffle=False)

    mp = nn.BondMessagePassing(d_h=message_hidden_dim, depth=depth, dropout=dropout)
    agg = nn.MeanAggregation()
    # output_transform = nn.UnscaleTransform.from_standard_scaler(scaler)
    # ffn = nn.RegressionFFN(output_transform=output_transform, input_dim=message_hidden_dim, hidden_dim=ffn_hidden_dim, n_layers=ffn_num_layers)
    ffn = nn.RegressionFFN(
        n_tasks=len(target_columns),
        output_transform=None, input_dim=message_hidden_dim, hidden_dim=ffn_hidden_dim, n_layers=ffn_num_layers,
        dropout=dropout
    )
    batch_norm = True
    metric_list = [nn.metrics.MAE(), nn.metrics.R2Score()]
    model = models.MPNN(mp, agg, ffn, batch_norm, metric_list)

    trainer = pl.Trainer(
        accelerator="auto",
        devices=1,
        max_epochs=200, # number of epochs to train for
        # below are needed for Ray and Lightning integration
        strategy=RayDDPStrategy(),
        callbacks=[RayTrainReportCallback()],
        plugins=[RayLightningEnvironment()],
        enable_progress_bar=False,
        enable_checkpointing=False
    )

    trainer = prepare_trainer(trainer)
    trainer.fit(model, train_loader, val_loader)

## Define parameter search space

In [9]:
search_space = {
    "depth": tune.qrandint(lower=2, upper=6, q=1),
    "ffn_hidden_dim": tune.qrandint(lower=300, upper=2400, q=100),
    "ffn_num_layers": tune.qrandint(lower=1, upper=3, q=1),
    "message_hidden_dim": tune.qrandint(lower=300, upper=2400, q=100),
}

In [10]:
ray.shutdown()
ray.init(include_dashboard=False)

scheduler = FIFOScheduler()

# Scaling config controls the resources used by Ray
scaling_config = ScalingConfig(
    num_workers=1,
    use_gpu=True, # set to True if you want to use GPU
)

# Checkpoint config controls the checkpointing behavior of Ray
checkpoint_config = CheckpointConfig(
    num_to_keep=1, # number of checkpoints to keep
    checkpoint_score_attribute="val_loss", # Save the checkpoint based on this metric
    checkpoint_score_order="min", # Save the checkpoint with the lowest metric value
    checkpoint_frequency=0,        # Do not checkpoint during training
)

run_config = RunConfig(
    checkpoint_config=checkpoint_config,
    storage_path=(hpopt_save_dir / "ray_results").absolute(), # directory to save the results
)

ray_trainer = TorchTrainer(
    lambda config: train_model(
        # config, train_dset, val_dset, num_workers, scaler
        config, train_dset, val_dset, num_workers
    ),
    scaling_config=scaling_config,
    run_config=run_config,
)

search_alg = HyperOptSearch(
    n_initial_points=10, # number of random evaluations before tree parzen estimators
    random_state_seed=RANDOM_SEED,
)

# OptunaSearch is another search algorithm that can be used
# search_alg = OptunaSearch()

tune_config = tune.TuneConfig(
    metric="val_loss",
    mode="min",
    num_samples=30, # number of trials to run
    scheduler=scheduler,
    search_alg=search_alg,
    trial_dirname_creator=lambda trial: str(trial.trial_id), # shorten filepaths
)

tuner = tune.Tuner(
    ray_trainer,
    param_space={
        "train_loop_config": search_space,
    },
    tune_config=tune_config,
)

# Start the hyperparameter search
results = tuner.fit()

(raylet) [2025-03-11 18:56:05,196 E 368769 368805] (raylet) file_system_monitor.cc:116: /var/tmp/ray/session_2025-03-11_18-55-53_413230_368506 is over 95% full, available space: 13.2578 GB; capacity: 295.046 GB. Object creation will fail if spilling is required.
(RayTrainWorker pid=370041) Setting up process group for: env:// [rank=0, world_size=1]
(TorchTrainer pid=369812) Started distributed worker processes: 
(TorchTrainer pid=369812) - (node_id=e64f6aa7699495c25085c0ee455fef71542cc05e47e06af90d1756f6, ip=10.128.0.3, pid=370041) world_rank=0, local_rank=0, node_rank=0
(RayTrainWorker pid=370041) /opt/conda/envs/admet/lib/python3.11/site-packages/ray/train/lightning/_lightning_utils.py:262: This API is deprecated and may be removed in future Ray releases. You could suppress this warning by setting env variable PYTHONWARNINGS="ignore::DeprecationWarning"
(RayTrainWorker pid=370041) `get_trial_name` is deprecated because the concept of a `Trial` will soon be removed in Ray Train.Ray Tr

## Hyperparameter optimization results

In [14]:
# results of all trials
result_df = results.get_dataframe()
results_df = result_df.sort_values('val/mae')
results_df

train_loss  train_loss_step   val/mae    val/r2  val_loss  \
20    0.111647         0.196051  0.333945  0.772035  0.212032   
16    0.118982         0.246708  0.338588  0.775903  0.208435   
22    0.105982         0.188439  0.343046  0.776747  0.207649   
25    0.112025         0.207468  0.344700  0.767732  0.216034   
2     0.128368         0.324513  0.346323  0.770218  0.213722   
24    0.095113         0.196374  0.346530  0.762592  0.220816   
18    0.123027         0.254524  0.348388  0.770337  0.213612   
21    0.118977         0.232637  0.352570  0.757551  0.225504   
29    0.126928         0.157115  0.359399  0.756538  0.226446   
17    0.141470         0.109609  0.359909  0.769166  0.214700   
28    0.130800         0.177318  0.362293  0.743070  0.238973   
10    0.135570         0.279438  0.365569  0.746793  0.235510   
12    0.163534         0.161356  0.365676  0.738973  0.242783   
3     0.141506         0.151756  0.369101  0.738415  0.243303   
19    0.107998         0.217676  0.371113  0.727779  0.253195   
23    0.120686         0.200806  0.378520  0.725485  0.255329   
6     0.156881         0.168639  0.379580  0.726425  0.254455   
27    0.135485         0.183568  0.379813  0.726681  0.254217   
13    0.110241         0.316646  0.382407  0.721391  0.259136   
5     0.125283         0.153953  0.384293  0.715115  0.264974   
14    0.140904         0.243290  0.388111  0.715019  0.265063   
1     0.144600         0.482701  0.392977  0.717137  0.263094   
9     0.119270         0.175806  0.393446  0.712239  0.267649   
26    0.177259         0.233706  0.396946  0.702251  0.276939   
11    0.123163         0.199507  0.404543  0.709075  0.270592   
15    0.194827         0.388775  0.414797  0.706194  0.273271   
0     0.143215         0.200856  0.423597  0.680509  0.297161   
7     0.153079         0.171856  0.426103  0.673674  0.303518   
4     0.247264         0.354404  0.429526  0.654746  0.321124   
8     0.133326         0.140617  0.450431  0.639833  0.334995   

    train_loss_epoch  epoch  step   timestamp checkpoint_dir_name  ...  \
20          0.111647    199  1200  1741723256   checkpoint_000199  ...   
16          0.118982    199  1200  1741722724   checkpoint_000199  ...   
22          0.105982    199  1200  1741723682   checkpoint_000199  ...   
25          0.112025    199  1200  1741724454   checkpoint_000199  ...   
2           0.128368    199  1200  1741719912   checkpoint_000199  ...   
24          0.095113    199  1200  1741724183   checkpoint_000199  ...   
18          0.123027    199  1200  1741722943   checkpoint_000199  ...   
21          0.118977    199  1200  1741723395   checkpoint_000199  ...   
29          0.126928    199  1200  1741725669   checkpoint_000199  ...   
17          0.141470    199  1200  1741722823   checkpoint_000199  ...   
28          0.130800    199  1200  1741725411   checkpoint_000199  ...   
10          0.135570    199  1200  1741721679   checkpoint_000199  ...   
12          0.163534    199  1200  1741721919   checkpoint_000199  ...   
3           0.141506    199  1200  1741720187   checkpoint_000199  ...   
19          0.107998    199  1200  1741723083   checkpoint_000199  ...   
23          0.120686    199  1200  1741723863   checkpoint_000199  ...   
6           0.156881    199  1200  1741720877   checkpoint_000199  ...   
27          0.135485    199  1200  1741725103   checkpoint_000199  ...   
13          0.110241    199  1200  1741722078   checkpoint_000199  ...   
5           0.125283    199  1200  1741720659   checkpoint_000199  ...   
14          0.140904    199  1200  1741722225   checkpoint_000199  ...   
1           0.144600    199  1200  1741719822   checkpoint_000199  ...   
9           0.119270    199  1200  1741721576   checkpoint_000199  ...   
26          0.177259    199  1200  1741724774   checkpoint_000199  ...   
11          0.123163    199  1200  1741721810   checkpoint_000199  ...   
15          0.194827    199  1200  1741722598   checkpoint_00019

In [ ]:
results_df.to_csv(hpopt_save_dir / 'results.csv', index=False)

In [ ]:
ray.shutdown()